In [106]:
from sympy import *
from sympy import lambdify, DiracDelta
import numpy as np
import plotly.graph_objects as go
from IPython.display import display, Math
from scipy.integrate import odeint

Введите свою функцию $W_р$(s) разомкнутой системы:

In [146]:
# Define open-loop transfer function W_open(s)
s = Symbol('s')

#↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓↓
W_open = (0.3*s+1) / ((0.25*s+1)*(0.04*s**2+0.07*s+1))
#↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑↑

# Display open-loop transfer function W_open(s)
display(Math('W_\\text{р}(s) = ' + latex(W_open)))

# Print as LaTeX code for copy-paste to LaTeX document
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №1\x1b[0m:')
print('\\begin{equation}' + '\n' + '\t' + 'W_\\text{р}(s) = ' +  latex(W_open) + '.' + '\n' + '\t' + '\\label{open_loop_initial}' + '\n' + '\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №1:
\begin{equation}
	W_\text{р}(s) = \frac{0.3 s + 1}{\left(0.25 s + 1\right) \left(0.04 s^{2} + 0.07 s + 1\right)}.
	\label{open_loop_initial}
\end{equation}


Шаг по времени для моделирования:

In [147]:
Y_open = fraction(W_open)[0]
U_open = fraction(W_open)[1]
factors = factor_list(Y_open)[1] + factor_list(U_open)[1]

# Min of time constants
tau = min([pow(factor[0].coeff(s, degree(factor[0], s)), 1/degree(factor[0], s)) for factor in factors])

# Display time constant
display(Math('\\tau = ' + latex(tau)))

# Print as LaTeX code for copy-paste to LaTeX document
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №7\x1b[0m:')
print('\\begin{equation}' + '\n' + '\t' + '\\tau = ' +  latex(tau) + '\n' + '\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №7:
\begin{equation}
	\tau = 0.2
\end{equation}


Приведение передаточной функции разомкнутой системы к виду для составления системы дифференциальных уравнений:

In [134]:
# Define normalize open-loop transfer function W_open(s)
Y_open = (fraction(W_open)[0]).expand()
U_open = (fraction(W_open)[1]).expand()
a = U_open.coeff(s, degree(U_open, s))
Y_open = (Y_open / a).simplify()
U_open = (U_open / a).simplify()
W_open = Y_open / U_open

# Display open-loop transfer function W_open(s)
display(Math('W_\\text{р}(s) = ' + latex(W_open)))

# Print as LaTeX code for copy-paste to LaTeX document
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №2\x1b[0m:')
print('\\begin{equation}' + '\n' + '\t' + 'W_\\text{р}(s) = ' +  latex(W_open.simplify()) + '.' + '\n' + '\t' + '\\label{open_loop}' + '\n' + '\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №2:
\begin{equation}
	W_\text{р}(s) = \frac{30.0 s + 100.0}{1.0 s^{3} + 5.75 s^{2} + 32.0 s + 100.0}.
	\label{open_loop}
\end{equation}


Функция $W_з$(s) замкнутой системы:

In [139]:
# Define closed-loop transfer function W_closed(s)
Y_closed = (fraction(W_open)[0]).simplify()
U_closed = (fraction(W_open)[1] + fraction(W_open)[0]).simplify()
W_closed = Y_closed / U_closed

# Display closed-loop transfer function W_closed(s)
display(Math('W_\\text{з}(s) = ' + latex(W_closed)))

# Print as LaTeX code for copy-paste to LaTeX document
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №8\x1b[0m:')
print('\\begin{equation}' + '\n' + '\t' + 'W_\\text{з}(s) = ' +  latex(W_closed.simplify()) + '.' + '\n' + '\t' + '\\label{closed_loop}' + '\n' + '\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №8:
\begin{equation}
	W_\text{з}(s) = \frac{30.0 s + 100.0}{1.0 s^{3} + 5.75 s^{2} + 62.0 s + 200.0}.
	\label{closed_loop}
\end{equation}


Область подобия:

In [140]:
# Find roots of U_closed(s)
roots = solve(U_open + Y_open, s)
# Find similarity region as 1/max|root|
similarity_region = 1/max([abs(root) for root in roots])

# Display similarity region
display(Math('T < ' + latex(similarity_region)))

# Print as LaTeX code for copy-paste to LaTeX document
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №9\x1b[0m:')
print('\\begin{equation}' + '\n' + '\t' + 'T < ' +  latex(similarity_region) + '\n' + '\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №9:
\begin{equation}
	T < 0.135607704022952
\end{equation}


Составление системы дифференциальных уравнений из передаточной функции

In [112]:
# Define function y(t) and function u(t)
t = Symbol('t')
y = Function('y')(t)
u = Function('u')(t)

# Define system of differential equations from transfer function
def system_of_diff_eqs(W):
    # Define variables
    variables = []
    # Find Y(s) and U(s) from transfer function W(s)
    Y = fraction(W)[0].expand()
    U = fraction(W)[1].expand()
    # Define system of differential equations
    eqs = []
    # Define the order of U(s)
    n = degree(U, s)
    # Define x_1(t) = y(t)
    x_1 = Function('x_1')(t)
    # Add equations to the system
    for i in range(1, n):
        # Define x_i(t)
        x_i = Function('x_' + str(i))(t)
        # Define x_{i+1}(t)
        x_i_next = Function('x_' + str(i+1))(t)
        # Append new variable to the list of variables
        variables.append(x_i)
        # Append new equation to the system
        eqs.append(Eq(diff(x_i, t), -U.coeff(s, n-i)*x_1 + x_i_next + Y.coeff(s, n-i)*u)) 
    # Define x_n(t)
    x_n = Function('x_' + str(n))(t)
    # Append x_n(t) to the list of variables
    variables.append(x_n)
    # Append new equation to the system
    eqs.append(Eq(diff(x_n, t), -U.coeff(s, 0)*x_1 + Y.coeff(s, 0)*u))
    # Append last equation to the system
    eqs.append(Eq(y, x_1))
    # Return system of differential equations and list of variables
    return eqs, variables

Система дифференциальных уравнений для разомкнутой системы:

In [135]:
# Find system of differential equations from transfer function W_open(s)
eqs_open, variables = system_of_diff_eqs(W_open)

# Display system of differential equations
latex_str = '\\begin{cases}'
for i in range(len(eqs_open)):
    latex_str += latex(eqs_open[i]) + '\\\\'
latex_str += '\\end{cases}'
display(Math(latex_str))

# Print latex code of system of differential equations
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №3\x1b[0m:')
print('\\begin{equation}')
print('\t\\begin{cases}')
for i in range(len(eqs_open)-1):
    print('\t\t'+latex(eqs_open[i]) + '\\\\')
print('\t\t'+latex(eqs_open[-1]))
print('\t\\end{cases}')
print('\t\\label{open_loop_system}')
print('\\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №3:
\begin{equation}
	\begin{cases}
		\frac{d}{d t} \operatorname{x_{1}}{\left(t \right)} = - 5.75 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{2}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{2}}{\left(t \right)} = 30.0 u{\left(t \right)} - 32.0 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{3}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{3}}{\left(t \right)} = 100.0 u{\left(t \right)} - 100.0 \operatorname{x_{1}}{\left(t \right)}\\
		y{\left(t \right)} = \operatorname{x_{1}}{\left(t \right)}
	\end{cases}
	\label{open_loop_system}
\end{equation}


Система дифференциальных уравнений для замкнутой системы:

In [136]:
eqs_closed = eqs_open.copy()
for i in range(len(eqs_closed)):
    eqs_closed[i] = eqs_closed[i].subs(u, 'u(t)-x_1(t)')
    
# Display system of differential equations
latex_str = '\\begin{cases}'
for i in range(len(eqs_closed)):
    latex_str += latex(eqs_closed[i]) + '\\\\'
latex_str += '\\end{cases}'
display(Math(latex_str))

# Print latex code of system of differential equations
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №4\x1b[0m:')
print('\\begin{equation}')
print('\t\\begin{cases}')
for i in range(len(eqs_closed)-1):
    print('\t\t'+latex(eqs_closed[i]) + '\\\\')
print('\t\t'+latex(eqs_closed[-1]))
print('\t\\end{cases}')
print('\t\\label{closed_loop_system}')
print('\\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №4:
\begin{equation}
	\begin{cases}
		\frac{d}{d t} \operatorname{x_{1}}{\left(t \right)} = - 5.75 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{2}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{2}}{\left(t \right)} = 30.0 u{\left(t \right)} - 62.0 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{3}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{3}}{\left(t \right)} = 100.0 u{\left(t \right)} - 200.0 \operatorname{x_{1}}{\left(t \right)}\\
		y{\left(t \right)} = \operatorname{x_{1}}{\left(t \right)}
	\end{cases}
	\label{closed_loop_system}
\end{equation}


Система дифференциальных уравнений с ключём:

In [137]:
eqs_with_key = eqs_open.copy()
for i in range(len(eqs_with_key)):
    eqs_with_key[i] = eqs_with_key[i].subs(u, 'key(u(t)-x_1(t), t)')
    
# Display system of differential equations
latex_str = '\\begin{cases}'
for i in range(len(eqs_with_key)):
    latex_str += latex(eqs_with_key[i]) + '\\\\'
latex_str += '\\end{cases}'
display(Math(latex_str))

# Print latex code of system of differential equations
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №5\x1b[0m:')
print('\\begin{equation}')
print('\t\\begin{cases}')
for i in range(len(eqs_with_key)-1):
    print('\t\t'+latex(eqs_with_key[i]) + '\\\\')
print('\t\t'+latex(eqs_with_key[-1]))
print('\t\\end{cases}')
print('\t\\label{system_with_key}')
print('\\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №5:
\begin{equation}
	\begin{cases}
		\frac{d}{d t} \operatorname{x_{1}}{\left(t \right)} = - 5.75 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{2}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{2}}{\left(t \right)} = 30.0 \operatorname{key}{\left(u{\left(t \right)} - \operatorname{x_{1}}{\left(t \right)},t \right)} - 32.0 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{3}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{3}}{\left(t \right)} = 100.0 \operatorname{key}{\left(u{\left(t \right)} - \operatorname{x_{1}}{\left(t \right)},t \right)} - 100.0 \operatorname{x_{1}}{\left(t \right)}\\
		y{\left(t \right)} = \operatorname{x_{1}}{\left(t \right)}
	\end{cases}
	\label{system_with_key}
\end{equation}


Система дифференциальных уравнений с ключём и экстраполятором:

In [116]:
eqs_with_key_and_extr = eqs_open.copy()
for i in range(len(eqs_with_key_and_extr)):
    eqs_with_key_and_extr[i] = eqs_with_key_and_extr[i].subs(u, 'extr(key(u(t)-x_1(t), t), t)')
    
# Display system of differential equations
latex_str = '\\begin{cases}'
for i in range(len(eqs_with_key_and_extr)):
    latex_str += latex(eqs_with_key_and_extr[i]) + '\\\\'
latex_str += '\\end{cases}'
display(Math(latex_str))

# Print latex code of system of differential equations
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №6\x1b[0m:')
print('\\begin{equation}')
print('\t\\begin{cases}')
for i in range(len(eqs_with_key_and_extr)-1):
    print('\t\t'+latex(eqs_with_key_and_extr[i]) + '\\\\')
print('\t\t'+latex(eqs_with_key_and_extr[-1]))
print('\t\\end{cases}')
print('\t\\label{system_with_key_and_extr}')
print('\\end{equation}')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл:
\begin{equation}
	\begin{cases}
		\frac{d}{d t} \operatorname{x_{1}}{\left(t \right)} = - 5.75 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{2}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{2}}{\left(t \right)} = 30.0 \operatorname{extr}{\left(\operatorname{key}{\left(u{\left(t \right)} - \operatorname{x_{1}}{\left(t \right)},t \right)},t \right)} - 32.0 \operatorname{x_{1}}{\left(t \right)} + \operatorname{x_{3}}{\left(t \right)}\\
		\frac{d}{d t} \operatorname{x_{3}}{\left(t \right)} = 100.0 \operatorname{extr}{\left(\operatorname{key}{\left(u{\left(t \right)} - \operatorname{x_{1}}{\left(t \right)},t \right)},t \right)} - 100.0 \operatorname{x_{1}}{\left(t \right)}\\
		y{\left(t \right)} = \operatorname{x_{1}}{\left(t \right)}
	\end{cases}
	\label{system_with_key_and_extr}
\end{equation}


Определение констант

In [117]:
time = 10
if float(tau) > 0.001:
    tau = 0.001
ts = np.arange(0, time, float(tau))
u0 = lambda t: 1 if t>=0 else 0

Решение системы дифференциальных уравнений:

In [118]:
def key(u, t):
    if abs(floor(t/T+0.5)*T - t) < tau/2:
        return u/tau
    else:
        return 0

u_prev = 1

def extr(u, t):
    global u_prev
    if abs(floor(t/T+0.5)*T - t) < tau/2:
        u_prev = u*tau
    return u_prev

# RungeKutta1
def rungekutta1(f, y0, t, args=()):
    n = len(t)
    y = np.zeros((n, len(y0)))
    y[0] = y0
    for i in range(n - 1):
        h = t[i+1] - t[i]
        y[i+1] = y[i] + h*np.array(f(y[i], t[i], *args))
    return y

# Functions of right side of system of differential equations using lambdify
func_closed = lambdify((t, u, (variables)), [eq.rhs for eq in eqs_closed[:-1]])
func_key = lambdify((t, u, (variables)), [eq.rhs for eq in eqs_with_key[:-1]], {"key" : key})
func_key_and_extr = lambdify((t, u, (variables)), [eq.rhs for eq in eqs_with_key_and_extr[:-1]], {"key" : key, "extr" : extr})

# Define function for solving system of differential equations
def f_closed(y, t):
    return func_closed(t, u0(t), y)

def f_key(y, t):
    return func_key(t, u0(t), y)

def f_key_and_extr(y, t):
    return func_key_and_extr(t, u0(t), y)

# Find solution
solution_closed = rungekutta1(f_closed, np.zeros(len(variables)), ts)

Построение графиков для замкнутой системы:

In [119]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_closed[:, 0], name='y(t)', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))
fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_closed.pdf')
fig.show()

Построение графиков в области подобия

In [141]:
# Define quantization step multiple of tau and less than similarity_region in 10 times
T = (similarity_region/10)//tau*tau

# Display quantization step
display(Math('T = ' + latex(T)))

# Print latex code of quantization step
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №10, ВСТАВКА №13\x1b[0m:')
print('$T = ' + latex(T) + '$')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл вместо ВСТАВКА №10, ВСТАВКА №13:
$T = 0.013$


In [121]:
solution_key = rungekutta1(f_key, np.zeros(len(variables)), ts)
solution_key_and_extr = rungekutta1(f_key_and_extr, np.zeros(len(variables)), ts)

In [122]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_key[:, 0], name='y(t)', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))
fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_key_less_similarity_region.pdf')
fig.show()

In [123]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_closed[:, 0], name='y(t) непрерывной', line_shape='spline', line=dict(color='green', width=3)))
fig.add_trace(go.Scatter(x=ts, y=solution_key_and_extr[:, 0], name='y(t) дискретной', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))

fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_key_and_extr_less_similarity_region.pdf')
fig.show()

Построение графиков около области подобия

In [124]:
# Define quantization step multiple of tau and less than similarity_region in 10 times
T = (similarity_region)//tau*tau

# Display quantization step
display(Math('T = ' + latex(T)))

# Print latex code of quantization step
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №11, ВСТАВКА №14\x1b[0m:')
print('$T = ' + latex(T) + '$')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл:
$T = 0.135$


In [125]:
solution_key = rungekutta1(f_key, np.zeros(len(variables)), ts)
solution_key_and_extr = rungekutta1(f_key_and_extr, np.zeros(len(variables)), ts)

In [126]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_key[:, 0], name='y(t)', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))
fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_key_around_similarity_region.pdf')
fig.show()

In [127]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_closed[:, 0], name='y(t) непрерывной', line_shape='spline', line=dict(color='green', width=3)))
fig.add_trace(go.Scatter(x=ts, y=solution_key_and_extr[:, 0], name='y(t) дискретной', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))

fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_key_and_extr_around_similarity_region.pdf')
fig.show()

Построение графиков вне области подобия

In [128]:
# Define quantization step multiple of tau and less than similarity_region in 10 times
T = (similarity_region*3)//tau*tau

# Display quantization step
display(Math('T = ' + latex(T)))

# Print latex code of quantization step
print('Скопируйте код ниже и вставьте в свой LaTeX-файл вместо \x1b[31mВСТАВКА №12, ВСТАВКА №15\x1b[0m:')
print('$T = ' + latex(T) + '$')

<IPython.core.display.Math object>

Скопируйте код ниже и вставьте в свой LaTeX-файл:
$T = 0.406$


In [129]:
solution_key = rungekutta1(f_key, np.zeros(len(variables)), ts)
solution_key_and_extr = rungekutta1(f_key_and_extr, np.zeros(len(variables)), ts)

In [130]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_key[:, 0], name='y(t)', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))
fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_key_more_similarity_region.pdf')
fig.show()

In [131]:
# Plot solution using plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=ts, y=solution_closed[:, 0], name='y(t) непрерывной', line_shape='spline', line=dict(color='green', width=3)))
fig.add_trace(go.Scatter(x=ts, y=solution_key_and_extr[:, 0], name='y(t) дискретной', line_shape='spline', line=dict(color='blue', width=3)))
fig.add_trace(go.Scatter(x=ts, y=[u0(t) for t in ts], name='u(t)', line_shape='spline', line=dict(color='red', width=3)))

fig.update_layout(xaxis_title='t', yaxis_title='y(t), u(t)')
fig.update_layout(template='plotly_white')
fig.update_layout(font=dict(size=14))
fig.update_layout(width=680, height=420,
                    margin=dict(l=25, r=25, b=25, t=25, pad=4))
fig.write_image('solution_key_and_extr_more_similarity_region.pdf')
fig.show()